# 02806 Social Data Analysis and Visualizations - Final project: NYPD Motor Vehicle Collision
## By David Frich Hansen, s144242 and Peter Edsberg Møllgaard s144256
#### 09/05-2017


## 1. Motivation
The dataset we have chosen is the NYPD Motor Collision Dataset available for free as Open City Data for New York City. The dataset, along with documentation can be found [here](https://data.cityofnewyork.us/Public-Safety/NYPD-Motor-Vehicle-Collisions/h9gi-nx95 "NYPD Motor Vehicle Collisions"). The dataset is continuously updated. This project includes data over vehicle collisions from the 1st of July 2012 until the 31st of March 2017 inclusive. 

This is combined with weather data from the National Centers for Enviromental Information under NOAA, the National Oceanic and Atmospheric Administration. The used data can be found [here](https://www.ncdc.noaa.gov/cdo-web/datasets "NOAA Datasets") and is the Local Climatological Data, subset to only include the weather for the NYC Central Park Weather Station in the same time-period as the motor vehicle collision dataset.

Finally, to look at population densities we included data from [here](https://data.cityofnewyork.us/City-Government/New-York-City-Population-By-Neighborhood-Tabulatio/swpk-hqdp "NTA Population Densities") which includes number of residents in each Neighborhood Tabulation Area in NYC. These are the smallest easily available areas for which population densities is released. Similarly, GeoJSON shapefiles for these NTAs can be found [here](https://www1.nyc.gov/site/planning/data-maps/open-data/dwn-nynta.page "NTA GeoJSON Shapes").

We chose these datasets because they in combination allow us to take a look at some of the major causes and factors playing into car accidents, and whether or not these have consequences in terms of human life or human injuries. The raw NYPD-data allows us to investigate whether or not it's statistically more dangerous to ride a bike than to go by foot in different parts of the city, as well as allows us to determine whether or not weather plays a role in incidents. Finally, the population dataset allows us to look at specific places where accidents happen and hold this against how many people actually live here.

The goal with this analysis is to give the user (who is probably a resident of NYC) an idea as to whether or not he or she should grab his or her bike or go by foot depending on where they are. It should also be possible for them to look at the weather and then easily - based in the data - be able to asses the risk of being in a fatal accident. We should mention here, that the result of this particular part might be a bit off, as the classification is happening on the basis that the person is actually involved in an incident. However, as time is also included in this classification, it will still give the user an idea.

## 2. Basic statistics and data preprocessing

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from collections import Counter
import datetime as dt


%matplotlib inline


# Read data
collisions = pd.read_csv('NYPD_Motor_Vehicle_Collisions.csv', low_memory=False)

# Create datetime index
Dates = pd.to_datetime(collisions['DATE'])


In [2]:
# Read weather data (removed some columns in another script)
df_weather = pd.read_csv('Weather_removed_cols.csv', low_memory = False)
# create datetime index for weather
df_weather.index =pd.to_datetime(df_weather['DATE'])


In [3]:
# Prepare weather data with daily records instead of hourly
weather_full = pd.read_csv('CENTRALPARKWEATHERDATA.csv', low_memory=False)
weather_daily = weather_full[['DATE', 'DAILYMaximumDryBulbTemp', 'DAILYMinimumDryBulbTemp',
                              'DAILYPrecip','DAILYSnowfall',
                              'DAILYSnowDepth', 'DAILYAverageWindSpeed']].copy()

weather_daily.dropna(axis=0, how='all', subset =['DAILYMaximumDryBulbTemp', 'DAILYMinimumDryBulbTemp',
                                                 'DAILYPrecip','DAILYSnowfall',
                                                 'DAILYSnowDepth', 'DAILYAverageWindSpeed'], inplace=True)

# Get dates in the right format
weather_daily_dates = pd.to_datetime(weather_daily['DATE'])
weather_daily = weather_daily.assign(DATEASSTRING = weather_daily_dates.copy().map(lambda x : x.strftime("%m/%d/%Y")))

# Drop original date label
weather_daily.drop('DATE', axis = 1, inplace=True)


weather_daily = weather_daily.assign(DATEASDT = weather_daily_dates.copy().map(lambda x : x.date()))

# remove NaN's
weather_daily.dropna(axis=0 , how='any',subset=['DAILYMaximumDryBulbTemp', 'DAILYSnowfall'], inplace=True)



# Find missing dates in weather data
d = weather_daily_dates.map(lambda x : x.date()).tolist()
date_set = set(d[0] + dt.timedelta(x) for x in range((d[-1]-d[0]).days))
missing = sorted(date_set - set(d))
assert(len(missing) == 0)




In [4]:
# Join the NYPD-data and the weather-data on the date
weather_daily = weather_daily.rename(columns = {'DATEASSTRING' : 'DATE'})
full = pd.merge(collisions, weather_daily)

# write to csv
#full.to_csv('collisions_weather_merged.csv')

In [5]:
# Create json for incidents pr. day
collisions_heat = pd.Series([1 for i in range(collisions.shape[0])], index = Dates)
dateCount = collisions_heat.groupby(collisions_heat.index.date).count()
dateCount = pd.DataFrame(dateCount)
dateCount = dateCount.assign(date=dateCount.index.map(lambda x : x.strftime("%Y-%m-%d")))
dateCount.columns = ['count', 'date']
dateCount.to_json('Collisions_per_day.json', orient = "records")

In [6]:
# Create json for incidents pr. year
def getYear(string):
    return int(string.split('/')[-1])
year = collisions.DATE.map(getYear)

# Count number of incidents
cYear = sorted(Counter(year).items(), key= lambda x : x[0])

# Export to JSON
index, count = zip(*cYear)

collisionsYear = pd.DataFrame()
collisionsYear = collisionsYear.assign(indeces=index)
collisionsYear = collisionsYear.assign(count=count)
collisionsYear.to_json('incidents_per_year.json', orient = "records")

In [7]:
# Create json for incidents pr hour
def getHour(string):
    return int(string.split(':')[0])

# Count number of injures
hour = collisions.TIME.map(getHour)
cHour = sorted(Counter(hour).items(), key = lambda x : x[0])

# Export to JSON
index, count = zip(*cHour)

collisionsHour = pd.DataFrame()
collisionsHour = collisionsHour.assign(indeces = index)
collisionsHour = collisionsHour.assign(count=count)
collisionsHour.to_json('incident_per_hour.json', orient='records')

In [8]:
# create json for injuries pr. hour
collisions = collisions.assign(HOUR = hour)
collisionsTimesInjuries = collisions[['NUMBER OF PERSONS INJURED', 'HOUR']]
collisionsTimesInjuries = collisionsTimesInjuries.loc[collisionsTimesInjuries['NUMBER OF PERSONS INJURED'] > 0]

# Count amount of injuries
cHourInj = sorted(Counter(collisionsTimesInjuries.HOUR).items(), key = lambda x : x[0])

# Export to JSON
index, count = zip(*cHourInj)

collisionsTimesInjuries = pd.DataFrame()
collisionsTimesInjuries = collisionsTimesInjuries.assign(indeces = index)
collisionsTimesInjuries = collisionsTimesInjuries.assign(count = count)
collisionsTimesInjuries.to_json('injuries_per_hour.json', orient='records')



In [9]:
# create json for deaths pr. hour
collisionsTimesKilled = collisions[['NUMBER OF PERSONS KILLED', 'HOUR']]
collisionsTimesKilled = collisionsTimesKilled.loc[collisionsTimesKilled['NUMBER OF PERSONS KILLED'] > 0]

# Count number of deaths
cHourDeath = sorted(Counter(collisionsTimesKilled.HOUR).items(), key = lambda x : x[0])

# Export to JSON
index, count = zip(*cHourDeath)

collisionsTimesKilled = pd.DataFrame()
collisionsTimesKilled = collisionsTimesKilled.assign(indeces = index)
collisionsTimesKilled = collisionsTimesKilled.assign(count = count)
collisionsTimesKilled.to_json('deaths_per_hour.json', orient='records')

In [10]:
# Geodata for Chloropeth


#Edited from https://gis.stackexchange.com/questions/208546/check-if-a-point-falls-within-a-multipolygon-with-python
import geopandas
from shapely.geometry import Point

df = collisions.dropna(axis=0, how='any', subset=['LONGITUDE', 'LATITUDE'], inplace=False)[['LONGITUDE', 'LATITUDE']]

#Creating a shapefile containing Lon Lat of incidents
geometry = [Point(xy) for xy in zip(df.LONGITUDE, df.LATITUDE)]
df = df.drop(['LONGITUDE', 'LATITUDE'], axis=1)
crs = {'init': 'epsg:4326'}

#Calculating which NTA each incidents belong in
points = geopandas.GeoDataFrame(df, crs=crs, geometry=geometry)
poly  = geopandas.GeoDataFrame.from_file('ntasWPop.shp')
from geopandas.tools import sjoin
pointInPolys = sjoin(points, poly, how='left')
grouped = pointInPolys.groupby('index_right')

#Counting the amount of incidents in each NTA
data = list(grouped)
liste = [[],[]]
for i in range(len(data)):
    liste[0].append(str(data[i][1].NTAName.iloc[0]))
    liste[1].append(len(data[i][1].NTAName))
    
    
df_incidents_per_NTA = pd.DataFrame()
df_incidents_per_NTA = df_incidents_per_NTA.assign(NTAName=liste[0])
df_incidents_per_NTA = df_incidents_per_NTA.assign(count=liste[1])

In [11]:
# Population data for density plots

import json

with open('./Population/ntas.geojson') as f:
    ntaShapes = json.load(f)
    # Number of NTA's
    num = len(ntaShapes['features'])    
    # Read population data
    popData = pd.read_csv('./Population/population.csv', low_memory=False)
    # Get only data from 2010
    popData = popData.loc[popData['Year'] > 2001]
    s = 0
    # For each NTA
    for nta in range(num):
        # Get name of NTA
        name = ntaShapes['features'][nta]['properties']['NTAName']
        
        # Find the name in population data
        row = popData.loc[popData['NTA Name'] == name]
        
        # Amount of incidents
        inc = df_incidents_per_NTA[df_incidents_per_NTA['NTAName']==name]['count'].tolist()
        s += float(ntaShapes['features'][nta]['properties']['Shape__Area'])
        
        # If row is empty
        if row.empty:
            ntaShapes['features'][nta]['properties']['population'] = str(0)
            ntaShapes['features'][nta]['properties']['count'] = str(inc)
        else:
            # Get population in that NTA
            pop = row['Population'].tolist()[0]

            # Set that value in the json
            ntaShapes['features'][nta]['properties']['population'] = str(pop)
            ntaShapes['features'][nta]['properties']['count'] = str(inc)
    print s
    # dump json
    with open('ntasWPop.json', 'w') as out:
        json.dump(ntaShapes, out)

0.0834347415323


## 3. Theory and analysis



### KNN to determine decision boundaries to determine whether or not walking or biking in different parts of NYC is more safe

In [12]:
# Remove observations not in NYC
collisions = collisions[np.abs(collisions.LONGITUDE-collisions.LONGITUDE.mean())<=(2.05*collisions.LONGITUDE.std())]
collisions = collisions[np.abs(collisions.LATITUDE-collisions.LATITUDE.mean())<=(2.05*collisions.LATITUDE.std())]


# Create dataframe with locations, number of pedestrians injured/killed and number of cyclists injured or killed
bikeOrWalk = collisions[(collisions['NUMBER OF PEDESTRIANS INJURED'] != 0) | (collisions['NUMBER OF PEDESTRIANS KILLED'] != 0) |
                       (collisions['NUMBER OF CYCLIST KILLED'] != 0) | (collisions['NUMBER OF CYCLIST INJURED'] != 0)] 
# Select columns
bikeOrWalk = bikeOrWalk[['LONGITUDE', 'LATITUDE', 'NUMBER OF PEDESTRIANS INJURED', 'NUMBER OF PEDESTRIANS KILLED', 
                         'NUMBER OF CYCLIST INJURED', 'NUMBER OF CYCLIST KILLED']]

# Remove NaNs from location
bikeOrWalk.dropna(axis=0, how='any', subset=['LONGITUDE', 'LATITUDE'], inplace=True)


# Select categories for each observation based on the amount of people injured or killed.
cat = []
pedsIL = bikeOrWalk['NUMBER OF PEDESTRIANS INJURED'].tolist()
pedsKL = bikeOrWalk['NUMBER OF PEDESTRIANS KILLED'].tolist()
cycsIL = bikeOrWalk['NUMBER OF CYCLIST INJURED'].tolist()
cycsKL = bikeOrWalk['NUMBER OF CYCLIST KILLED'].tolist()

for i in range(bikeOrWalk.shape[0]):
    peds = pedsIL[i] + pedsKL[i]
    cycs = cycsIL[i] + cycsKL[i]
    if peds < cycs:
        cat.append('Cyclist accident.')
    elif cycs < peds:
        cat.append('Pedestrian accident.')
    else:
        cat.append('Both.')

bikeOrWalk = bikeOrWalk.assign(CATEGORY = cat)

In [13]:
import sklearn.neighbors as nb
import geoplotlib as gpl
from sklearn import model_selection
# Function that trains a KNN-classifier, cross-validates the number of neighbors using a grid-search strategy and 
# plots a map, as geodata is used
def KNNClassify(k = 10, maxNeighbors = 10, plot=True, gridSize=75):
    

    # Y as target
    Y, YLabels = pd.factorize(bikeOrWalk.CATEGORY)
        
    
    # X as features (ie. location)
    X = zip(bikeOrWalk.LONGITUDE.tolist(), bikeOrWalk.LATITUDE.tolist())
    X = np.asarray(X).astype(np.float)
    
    # Grid for the parameter
    grid = {'n_neighbors': np.arange(1, maxNeighbors + 1)}
    # Cross-validate with accuracy as metric using stratified K fold as splitting strategy.
    cv_Res = model_selection.GridSearchCV(nb.KNeighborsClassifier(), grid, scoring=None, 
                                          fit_params=None, n_jobs=-1, 
                                          iid=False, refit=True, cv=k, 
                                          verbose=1, pre_dispatch='2*n_jobs', 
                                          error_score='raise', return_train_score=True)
    
    # Fit best model
    cv_Res.fit(X, Y)
    # Best parameter
    neigh = cv_Res.best_estimator_
    k_opt = cv_Res.best_params_
    print "Best parameter: " + repr(k_opt)
   
   
    
    # Set boundaries for plot
    north=np.amax(collisions.LATITUDE)
    west=np.amin(collisions.LONGITUDE)
    south=np.amin(collisions.LATITUDE)
    east=np.amax(collisions.LONGITUDE)
    y_max = north
    x_max = east
    y_min = south
    x_min = west

    
    
    # Create grid for prediction with size gridSize x gridSize. Constants chosen by trial and error
    gridX = np.linspace(x_min, x_max, gridSize)
    gridY = np.linspace(y_min, y_max, gridSize)
    xx, yy = np.meshgrid(gridX, gridY)
    
    # Predict on the grid
    Z = neigh.predict(np.c_[xx.ravel(), yy.ravel()])
    Z = Z.reshape(xx.shape)
    
    # Take out 3 dictionaries for plotting geodata
    index = {'class1':{'lon': [],'lat': []},'class2':{'lon': [],'lat': []},'class3':{'lon': [],'lat': []}}
    class_name = ['class1','class2','class3']
    step_size_lon = (x_max - x_min)/gridSize
    step_size_lat = (y_max - y_min)/gridSize
    for i in range(len(gridX)):
        for j in range(len(gridY)):
            index[class_name[Z[j][i]]]['lon'].append(x_min+step_size_lon*i)
            index[class_name[Z[j][i]]]['lat'].append(y_min+step_size_lat*j)
    if plot:

        # Plot grid
        gpl.dot(index['class1'], color=[255,255,0])
        gpl.dot(index['class2'], color=[255,0,0])
        gpl.dot(index['class3'], color=[0,255,0])

        gpl.set_bbox(gpl.utils.BoundingBox(north=north, south=south, east=east, west=west))
        gpl.inline()

    return index

    
    


In [14]:
resKNN = KNNClassify(k=20, maxNeighbors=50, gridSize=85, plot=True)

c1 = pd.DataFrame()
c1 = c1.assign(longitude = resKNN['class1']['lon'])
c1 = c1.assign(latitude = resKNN['class1']['lat'])
c1 = c1.assign(cl = np.ones_like(c1.latitude, dtype=int))


c2 = pd.DataFrame()
c2 = c2.assign(longitude = resKNN['class2']['lon'])
c2 = c2.assign(latitude = resKNN['class2']['lat'])
c2 = c2.assign(cl = 2*np.ones_like(c2.latitude, dtype=int))

c3 = pd.DataFrame()
c3 = c3.assign(longitude = resKNN['class3']['lon'])
c3 = c3.assign(latitude = resKNN['class3']['lat'])
c3 = c3.assign(cl = 3*np.ones_like(c3.latitude, dtype=int))


# Merge dataframes
resKNN = pd.concat([c1, c2, c3])
resKNN.index = range(len(resKNN.index))
resKNN.columns = ['longitude', 'latitude', 'class']
# Export to json
resKNN.to_json('./resultKNN.json', orient='records')


Fitting 20 folds for each of 50 candidates, totalling 1000 fits


[Parallel(n_jobs=-1)]: Done  34 tasks      | elapsed:    3.9s
[Parallel(n_jobs=-1)]: Done 184 tasks      | elapsed:   18.9s
[Parallel(n_jobs=-1)]: Done 434 tasks      | elapsed:   55.2s
[Parallel(n_jobs=-1)]: Done 784 tasks      | elapsed:  2.0min
[Parallel(n_jobs=-1)]: Done 1000 out of 1000 | elapsed:  2.8min finished


Best parameter: {'n_neighbors': 36}


### Decision trees

In [15]:
from sklearn.ensemble import RandomForestClassifier

# Select relevant columns
weather_accidents = full[['TIME', 'NUMBER OF PERSONS INJURED', 'NUMBER OF PERSONS KILLED', 'DAILYMaximumDryBulbTemp',
                          'DAILYMinimumDryBulbTemp', 'DAILYPrecip', 'DAILYSnowfall', 'DAILYSnowDepth', 'DAILYAverageWindSpeed']].copy()
weather_accidents = weather_accidents.assign(HOUR = weather_accidents.TIME.map(lambda x : int(x.split(':')[0])))
# Drop NaN's
weather_accidents = weather_accidents.dropna(how='any')

# Remove 'trace amounts' and set them to 0
weather_accidents = weather_accidents.replace(['T', 'Ts'], ['0', '0'])

# We need floats as datatype for classification
weather_accidents['DAILYMinimumDryBulbTemp'] = weather_accidents.DAILYMinimumDryBulbTemp.copy().astype(float)
weather_accidents['DAILYMaximumDryBulbTemp'] = weather_accidents.DAILYMaximumDryBulbTemp.copy().astype(float)
weather_accidents['DAILYPrecip'] = weather_accidents.DAILYPrecip.copy().astype(float)
weather_accidents['DAILYSnowfall'] = weather_accidents.DAILYSnowfall.copy().astype(float)
weather_accidents['DAILYSnowDepth'] = weather_accidents.DAILYSnowDepth.copy().astype(float)
weather_accidents['DAILYAverageWindSpeed'] = weather_accidents.DAILYAverageWindSpeed.copy().astype(float)

# Random forest instance
RFC = RandomForestClassifier(n_estimators=100, criterion='gini', max_depth=None, min_samples_split=2, 
                            min_samples_leaf=1, min_weight_fraction_leaf=0.0, max_features='auto', 
                            max_leaf_nodes=None, min_impurity_split=1e-07, bootstrap=True, oob_score=True, 
                            n_jobs=-1, random_state=None, verbose=1, warm_start=False, class_weight=None)

# Put into classes: "Risk of injury", "Risk of death", "Risk of injury or death", "Risk of involved in incident"
numInjured = weather_accidents['NUMBER OF PERSONS INJURED'].tolist()
numKilled = weather_accidents['NUMBER OF PERSONS KILLED'].tolist()
cat = []
for i in range(weather_accidents.shape[0]):
    if (numInjured[i] > 0) and (numKilled[i] == 0):
        cat.append('Risk of injury.')
    elif (numInjured[i] == 0) and (numKilled[i] > 0):
        cat.append('Risk of death.')
    elif (numInjured[i] > 0) and (numKilled[i] > 0):
        cat.append('Risk of injury or death.')
    else:
        cat.append('Risk of involved in incident.')
weather_accidents = weather_accidents.assign(CLASS = cat)

# Matrix with attributes
X = weather_accidents[['HOUR', 'DAILYMaximumDryBulbTemp', 'DAILYMinimumDryBulbTemp', 'DAILYPrecip', 'DAILYSnowfall', 'DAILYSnowDepth',
                      'DAILYSnowDepth', 'DAILYAverageWindSpeed']].as_matrix()

# Train classifier
RFC.fit(X, weather_accidents.CLASS.tolist())
RFC.oob_score_

[Parallel(n_jobs=-1)]: Done  34 tasks      | elapsed:    9.8s
[Parallel(n_jobs=-1)]: Done 100 out of 100 | elapsed:   23.3s finished


0.80905471015148867

## 4. Visualizations

## 5. Discussion and conclusions